<strong><b><font size="5">Furto de Veiculos na Cidade de São Paulo - Parte 2</font></b></strong>

Nessa segunda parte será construido uma mapa com as ocorrencias de furto de veiculos
No final será feito tambem um cálculo de distancias visando medir a proximididade das ocorrencias de furto com as unidades de segurança utilizando 3 escalas: 
<br>1-Menos de 500m
<br>2-De 500m até 1km
<br>3-De 1k até 1,5km


![title](dados/logoprojeto.png)

In [1]:
# As novas versões do Pandas e Matplotlib trazem diversas mensagens de aviso ao desenvolvedor. Vamos desativar isso.
import sys
import warnings
import matplotlib.cbook
if not sys.warnoptions:
    warnings.simplefilter("ignore")
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings("ignore", category=FutureWarning)
warnings.filterwarnings("ignore", category=matplotlib.cbook.mplDeprecation)

# Imports para manipulação de dados
import re
import json
import time
import numpy as np
import pandas as pd

In [2]:
#carregar os datasets
df_furtos = pd.read_csv('dados/df_furtos.csv',sep=';' )
df_unid_pm = pd.read_csv('dados/df_unid_PM.csv')
df_unid_gcm = pd.read_csv('dados/df_unid_GCM.csv')
df_unid_pcivil = pd.read_csv('dados/df_unid_pcivil.csv')

In [3]:
#criar a coluna para diferenciar nas legendas
df_furtos['TIPO']='Ocorrencia Furto'
df_unid_pm['TIPO'] = 'Policia Militar'
df_unid_gcm['TIPO'] = 'Guarda Civil Metr.'
df_unid_pcivil['TIPO'] = 'Policia Civil'

In [4]:
#fazer um merge com os Dfs com as unidades de policia
df_seg_unids = df_unid_pm.append([df_unid_gcm,df_unid_pcivil],ignore_index=True)

In [5]:
#Renomear as colunas
df_seg_unids = df_seg_unids.rename(columns={"eq_nome": "DESCR","eq_enderec": "LOGRADOURO", "latitude": "LATITUDE", "longitude": "LONGITUDE"}, errors="raise")

In [6]:
#Copiar as colunas para outro DF
df_analise = df_seg_unids[['DESCR', 'LOGRADOURO', 'LATITUDE','LONGITUDE','TIPO']].copy()
df_analise.tail()

DESCR  \
287             59º DISTRITO POLICIAL DE JARDIM NOEMIA   
288                 70º DISTRITO POLICIAL DE SÃO PAULO   
289             97º DISTRITO POLICIAL - AMERICANOPOLIS   
290  DEATUR - 3ª DELEGACIA DE POLÍCIA DO AEROPORTO ...   
291          DEIC - DELEGACIA DE INVESTIGAÇÃO CRIMINAL   

                         LOGRADOURO   LATITUDE  LONGITUDE           TIPO  
287  R VISTOSA DA MADRE DE DEUS 120 -23.487589 -46.410149  Policia Civil  
288      R. OTAVIO ALVES DUNDAS 390 -23.598729 -46.533290  Policia Civil  
289        ROD DOS IMIGRANTES KM 11 -23.650123 -46.631479  Policia Civil  
290                 ROD HELIO SMIDT -23.459182 -46.491205  Policia Civil  
291               ZAKI NARCHIAV 152 -23.512114 -46.622725  Policia Civil

In [7]:
#copiar a coluna descrição veiculo para desc
df_furtos['DESCR']  = df_furtos['DESCR_TIPO_VEICULO']


In [8]:
df_furtos.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7755 entries, 0 to 7754
Data columns (total 52 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   ANO_BO                    7755 non-null   int64  
 1   NUM_BO                    7755 non-null   int64  
 2   NUMERO_BOLETIM            7755 non-null   object 
 3   BO_INICIADO               7755 non-null   object 
 4   BO_EMITIDO                7755 non-null   object 
 5   DATAOCORRENCIA            7755 non-null   object 
 6   HORAOCORRENCIA            7280 non-null   object 
 7   PERIDOOCORRENCIA          7755 non-null   object 
 8   DATACOMUNICACAO           7755 non-null   object 
 9   DATAELABORACAO            7755 non-null   object 
 10  BO_AUTORIA                7755 non-null   object 
 11  FLAGRANTE                 7755 non-null   object 
 12  NUMERO_BOLETIM_PRINCIPAL  173 non-null    object 
 13  LOGRADOURO                7755 non-null   object 
 14  NUMERO  

In [9]:
#copio apenas as colunas relevantes 
df_analise_temp = df_furtos[['DESCR', 'LOGRADOURO', 'LATITUDE','LONGITUDE','TIPO']].copy()

In [10]:
df_analise_temp.head()

DESCR                                LOGRADOURO   LATITUDE  LONGITUDE  \
0  AUTOMOVEL                 RUA DOUTOR NEMEZIO BAILAO -23.575585 -46.775864   
1  AUTOMOVEL                              RUA DA UNIÃO -23.631312 -46.483268   
2  MOTOCICLO           AVENIDA SENADOR VITORINO FREIRE -23.686023 -46.633444   
3  AUTOMOVEL    RUA ANTONIO BORGES MACHADO DE OLIVEIRA -23.698705 -46.636175   
4  AUTOMOVEL  AVENIDA ENGENHEIRO ARMANDO DE ARRUDA PER -23.632395 -46.645789   

               TIPO  
0  Ocorrencia Furto  
1  Ocorrencia Furto  
2  Ocorrencia Furto  
3  Ocorrencia Furto  
4  Ocorrencia Furto

In [11]:
df_analise = df_analise.append([df_analise_temp],ignore_index=True)

In [12]:
df_analise.tail()

DESCR                LOGRADOURO   LATITUDE  LONGITUDE  \
8042   MOTONETA        RUA CESARIO GALERO -23.536308 -46.559807   
8043  AUTOMOVEL     RUA SOARES DE AVELLAR -23.629802 -46.639859   
8044  AUTOMOVEL  AVENIDA MARIO LOPES LEAO -23.653262 -46.719373   
8045  AUTOMOVEL  AVENIDA MARIO LOPES LEAO -23.653262 -46.719373   
8046  AUTOMOVEL    ESTRADA DE ITAPECERICA -23.646386 -46.747025   

                  TIPO  
8042  Ocorrencia Furto  
8043  Ocorrencia Furto  
8044  Ocorrencia Furto  
8045  Ocorrencia Furto  
8046  Ocorrencia Furto

Carregar os pacotes para plotagem do mapa

In [13]:
# Plotly
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff
from plotly.colors import n_colors
from plotly.subplots import make_subplots

# Supress warnings
import sys
import warnings

if not sys.warnoptions:
    warnings.simplefilter("ignore")

In [14]:
#Aqui faço o scatter plot com mapa do df_analise
fig = px.scatter_mapbox(df_analise, 
                        lat = "LATITUDE", 
                        title="Mapa de Furtos de Carros na cidade de São Paulo",
                       
                        lon = "LONGITUDE", 
                        hover_name = "DESCR",
                        color='TIPO',
                        hover_data = ["LOGRADOURO"],
                        color_discrete_sequence = ["red","blue","yellow","black"],
                        #labels={"furto": "Legenda"},
                        zoom = 10,
                        center = dict(lat = -23.54692, lon = -46.63603),
                        height = 400)
# Configurações adicionais do Plot
fig.update_layout(mapbox_style = "carto-positron")
fig.update_traces(mode='markers', selector=dict(type='scattermapbox'))
fig.update_traces(marker_symbol='circle', selector=dict(type='scattermapbox'))
fig.update_traces(marker_size=4, selector=dict(type='scattermapbox'))
fig.update_layout(margin = {"r":0,"t":30,"l":0,"b":0})
fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01,
   bordercolor='rgb(100,100,100)',
   borderwidth=2
))
fig.show()


<b>Mapa finalizado!</b><br>



Vamos calcular a distancia de uma ocorrencia para com as unidades de segurança, vou segmentar em 3 escalas:<br> 
1-Menos de 500m<br>
2-De 500m até 1km<br>
3-De 1k até 1,5km<br>
Para calcular a distância entre as coordenadas vou utilizar a função geodesic() do pacote geopy.

Distancias entre os as ocorrencias

In [ ]:
!pip install geopy

In [15]:
# Imports
import geopy
from geopy.distance import geodesic

In [16]:
# Essa função vai calcular a distância entre as coordenadas de cada ocorrencia e de cada unidade de segurança
def calcula_distancia( unid_lat, unid_long,ocorrencia_lat, ocorrencia_long):
    
    # Coordenadas da ocorrencia
    coord_ocorrencia = (ocorrencia_lat, ocorrencia_long)
    
    # Coordenadas da unidade de segurança
    coord_unid = (unid_lat, unid_long)
    
    # Calcula a distância com a função do pacote geopy 
    # O cálculo será em milhas, pois é o padrão nos EUA
    try:
        distancia = geodesic(coord_unid,coord_ocorrencia).m
        return distancia
    except:
        pass

Loop para o cálculo da distância de pontos de vendas para locais de prisões (a execução da célula abaixo é demorada)

In [17]:
df_furtos.head()

ANO_BO  NUM_BO NUMERO_BOLETIM          BO_INICIADO           BO_EMITIDO  \
0    2021    1878      1878/2021  10/05/2021 15:01:55  10/05/2021 15:19:06   
1    2021     193       193/2021  19/03/2021 11:07:03  19/03/2021 11:28:31   
2    2021     743       743/2021  12/03/2021 09:07:49  12/03/2021 09:25:59   
3    2021     811       811/2021  19/03/2021 08:47:44  19/03/2021 08:51:52   
4    2021     953       953/2021  01/04/2021 14:57:21  01/04/2021 15:12:25   

  DATAOCORRENCIA HORAOCORRENCIA PERIDOOCORRENCIA DATACOMUNICACAO  \
0     09/05/2021          23:30          A NOITE      10/05/2021   
1     18/03/2021          09:30       PELA MANHÃ      19/03/2021   
2     11/03/2021          15:50          A TARDE      12/03/2021   
3     18/03/2021            NaN  EM HORA INCERTA      19/03/2021   
4     21/03/2021          02:30     DE MADRUGADA      01/04/2021   

        DATAELABORACAO  ... UF_VEICULO  CIDADE_VEICULO DESCR_COR_VEICULO  \
0  10/05/2021 15:01:55  ...         SP         BARUERI              Azul   
1  19/03/2021 11:07:03  ...         MG  BELO HORIZONTE             Prata   
2  12/03/2021 09:07:49  ...         SP         S.PAULO           Amarelo   
3  19/03/2021 08:47:44  ...         SP         S.PAULO             Cinza   
4  01/04/2021 14:57:21  ...         SP         DIADEMA             Prata   

     DESCR_MARCA_VEICULO  ANO_FABRICACAO ANO_MODELO DESCR_TIPO_VEICULO  \
0      VW/NOVO FOX TL MA          2015.0     2015.0          AUTOMOVEL   
1         FIAT/MOBI LIKE          2018.0     2019.0          AUTOMOVEL   
2  HONDA/CG 125 CARGO KS          2013.0     2013.0          MOTOCICLO   
3         FIAT/PALIO EDX          1996.0     1997.0          AUTOMOVEL   
4     GM/CELTA 4P SPIRIT          2005.0     2006.0          AUTOMOVEL   

      periodo              TIPO      DESCR  
0   maio-2021  Ocorrencia Furto  AUTOMOVEL  
1  marco-2021  Ocorrencia Furto  AUTOMOVEL  
2  marco-2021  Ocorrencia Furto  MOTOCICLO  
3  marco-2021  Ocorrencia Furto  AUTOMOVEL  
4  abril-2021  Ocorrencia Furto  AUTOMOVEL  

[5 rows x 52 columns]

In [19]:
#criar um df com as variaveis para fazer o calculo da distancia
df_furtos_dist = df_furtos[['TIPO','LATITUDE','LONGITUDE']]


In [20]:
# Reset do índice (organiza o índice no novo dataframe
df_furtos_dist.reset_index(drop = True, inplace = True)

In [21]:
df_furtos_dist.head(3)

TIPO   LATITUDE  LONGITUDE
0  Ocorrencia Furto -23.575585 -46.775864
1  Ocorrencia Furto -23.631312 -46.483268
2  Ocorrencia Furto -23.686023 -46.633444

loop para calcular as distancias de cada ocorrencia para cada unidade de segurança

In [23]:
%%time

# Para cada unidade de seguança calcula a distância para todas as ocorrencias
for unid_name, position in zip(list(df_seg_unids['DESCR'].values), range(len(df_seg_unids))):

    # Criamos uma lista de distâncias
    distance_list = []

    # Para cada prisão no dataframe de prisões...
    for ocorrencia in range(len(df_furtos_dist)):
        
        # Atribui os valores às variáveis
        unid_lat = df_seg_unids[df_seg_unids['DESCR'] == unid_name]['LATITUDE'].values
        unid_long = df_seg_unids[df_seg_unids['DESCR'] == unid_name]['LONGITUDE'].values
        ocorrencia_lat = df_furtos_dist['LATITUDE'][ocorrencia]
        ocorrencia_long = df_furtos_dist['LONGITUDE'][ocorrencia]
        
        # Calcula a distância com a função criada na célula anterior
        distance = calcula_distancia(unid_lat, unid_long, ocorrencia_lat, ocorrencia_long)

        # Faz o append da distância à lista de distâncias
        distance_list.append(distance)

    # Adicionamos ao dataframe de prisões a lista de distâncias
    df_furtos_dist[unid_name] = distance_list

Wall time: 1h 17min 19s


In [24]:
df_furtos_dist.head()

TIPO   LATITUDE  LONGITUDE  \
0  Ocorrencia Furto -23.575585 -46.775864   
1  Ocorrencia Furto -23.631312 -46.483268   
2  Ocorrencia Furto -23.686023 -46.633444   
3  Ocorrencia Furto -23.698705 -46.636175   
4  Ocorrencia Furto -23.632395 -46.645789   

   1º 6ºPELOTÃO DA 2ªCOMPANHIA DO 34ªBATALHÃO DA POLÍCIA MILITAR - SÃO PAULO  \
0                                        6873.986218                           
1                                       24121.298667                           
2                                       15256.347523                           
3                                       16354.113620                           
4                                        9689.848412                           

   ACADEMIA DE POLÍCIA MILITAR DO BARRO BRANCO  \
0                                 19583.004384   
1                                 22411.845273   
2                                 23650.232800   
3                                 25069.591498   
4                                 17867.917380   

   5ªCOMPANHIA DE POLÍCIA MILITAR-  - SÃO PAULO -   JARDIM AMÉRICA DA PENHA  \
0                                       23184.074773                          
1                                       13449.555881                          
2                                       19155.647975                          
3                                       20549.709793                          
4                                       14755.759308                          

   SEDE DO  7º BPM/M  \
0       12435.791281   
1       20137.204816   
2       15599.491709   
3       16948.292803   
4        9538.998844   

   50°BATALHÃO DA POLÍCIA MILITAR -   SÃO PAULO - VILA SÃO JOSÉ  \
0                                       19609.993117              
1                                       26089.766862              
2                                        9886.668006              
3                                        8841.504740              
4                                       13725.149442              

   CENTRO DE FORMAÇÃO E APERFEIÇOAMENTO DE PRAÇAS DA POLÍCIA MILITAR  \
0                                       19409.271032                   
1                                       15721.448580                   
2                                       17698.326621                   
3                                       19128.915067                   
4                                       12513.340075                   

   2ªCOMPANHIA DE POLÍCIA MILITAR-8º BPM/M  - SÃO PAULO - VILA GOMES CARDIM  \
0                                       24102.736744                          
1                                       11128.093036                          
2                                       18049.070906                          
3                                       19400.980051                          
4                                       14240.208370                          

   ...  7ª SECCIONAL-CENTRO EXECUCAO CARTAS PRECATORIAS  \
0  ...                                     31197.509190   
1  ...                                     11903.723520   
2  ...                                     24117.971602   
3  ...                                     25358.903735   
4  ...                                     21124.005237   

   50º DISTRITO POLICIAL-  ITAIM PAULISTA  \
0                            39502.864764   
1                            16582.070766   
2                            31423.292683   
3                            32547.283969   
4                            29099.040511   

   36º DISTRITO POLICIAL DA VILA MARIANA  DAP - DPA-NUCLEO ARQUIVO  \
0                           12766.825839              28425.257491   
1                           18053.865865              11659.938826   
2                           11970.208871               9729.490060   
3                           13326.699161               9551.203681   
4                            5920.767043              1

Agora vamos criar duas colunas, **ocorrencia_0Km** e **ocorrencia_1Km**, **ocorrencia_2_a_3Km**, que contarão o número de furtos de veiculos que estão dentro de ate 1 km, de 1km até 2 km 2 de 2 até 3km.

In [25]:
#criar o dataframe como transposta do principal, removendo as 3 colunas
df_furtos_dist_ocorr = df_furtos_dist.drop(['TIPO', 'LATITUDE', 'LONGITUDE'], axis = 1).T

In [26]:
df_furtos_dist_ocorr.tail()

0        1        2     \
59º DISTRITO POLICIAL DE JARDIM NOEMIA              38596.2  17581.2  31662.2   
70º DISTRITO POLICIAL DE SÃO PAULO                  24892.7  6251.59  14067.5   
97º DISTRITO POLICIAL - AMERICANOPOLIS              16889.9  15265.2  3981.07   
DEATUR - 3ª DELEGACIA DE POLÍCIA DO AEROPORTO I...  31801.8  19080.9  29017.5   
DEIC - DELEGACIA DE INVESTIGAÇÃO CRIMINAL             17144  19415.4  19291.9   

                                                       3        4        5     \
59º DISTRITO POLICIAL DE JARDIM NOEMIA              32847.1  28913.1  33131.1   
70º DISTRITO POLICIAL DE SÃO PAULO                  15257.4  12070.9  18544.5   
97º DISTRITO POLICIAL - AMERICANOPOLIS              5401.91  2446.81  10755.4   
DEATUR - 3ª DELEGACIA DE POLÍCIA DO AEROPORTO I...  30376.2  24842.3  27075.7   
DEIC - DELEGACIA DE INVESTIGAÇÃO CRIMINAL             20711  13527.8  12801.9   

                                                       6        7        8     \
59º DISTRITO POLICIAL DE JARDIM NOEMIA              32232.3  3014.33  24397.9   
70º DISTRITO POLICIAL DE SÃO PAULO                  14639.4  17473.5  13053.3   
97º DISTRITO POLICIAL - AMERICANOPOLIS              4813.01  28971.8  12492.2   
DEATUR - 3ª DELEGACIA DE POLÍCIA DO AEROPORTO I...  29732.5  11524.9  17760.1   
DEIC - DELEGACIA DE INVESTIGAÇÃO CRIMINAL           20123.1  23534.4  3504.05   

                                                       9     ...     7745  \
59º DISTRITO POLICIAL DE JARDIM NOEMIA              17969.6  ...  31075.8   
70º DISTRITO POLICIAL DE SÃO PAULO                  950.228  ...    22207   
97º DISTRITO POLICIAL - AMERICANOPOLIS              10984.9  ...    19883   
DEATUR - 3ª DELEGACIA DE POLÍCIA DO AEROPORTO I...  15931.6  ...  23015.6   
DEIC - DELEGACIA DE INVESTIGAÇÃO CRIMINAL           12371.4  ...  9744.04   

                                                       7746     7747     7748  \
59º DISTRITO POLICIAL DE JARDIM NOEMIA              5976.29  41349.9  41616.4   
70º DISTRITO POLICIAL DE SÃO PAULO                  14325.7  23763.9    24021   
97º DISTRITO POLICIAL - AMERICANOPOLIS              24805.5    12739  13173.6   
DEATUR - 3ª DELEGACIA DE POLÍCIA DO AEROPORTO I...  3593.97    38268  38713.5   
DEIC - DELEGACIA DE INVESTIGAÇÃO CRIMINAL           16055.7  26851.2    27511   

                                                       7749     7750     7751  \
59º DISTRITO POLICIAL DE JARDIM NOEMIA                36130  16209.2  28250.5   
70º DISTRITO POLICIAL DE SÃO PAULO                    18936  7424.43  11407.2   
97º DISTRITO POLICIAL - AMERICANOPOLIS              7435.59  14574.3   2407.6   
DEATUR - 3ª DELEGACIA DE POLÍCIA DO AEROPORTO I...  32084.5  11048.2  24237.7   
DEIC - DELEGACIA DE INVESTIGAÇÃO CRIMINAL           19837.8  6961.65    13151   

                                                       7752     7753     7754  
59º DISTRITO POLICIAL DE JARDIM NOEMIA              36512.8  36512.8  38627.4  
70º DISTRITO POLICIAL DE SÃO PAULO                    19926    19926  22440.4  
97º DISTRITO POLICIAL - AMERICANOPOLIS              8974.02  8974.02    11796  
DEATUR - 3ª DELEGACIA DE POLÍCIA DO AEROPORTO I...    31697    31697  33347.9  
DEIC - DELEGACIA DE INVESTIGAÇÃO CRIMINAL           18485.2  18485.2  19548.5  

[5 rows x 7755 columns]

In [27]:
#df.filter(like = 'index to keep', axis=0)
df_furtos_dist_ocorr.filter(like = '5ªCOMPANHIA DE POLÍCIA MILITAR- - SÃO PAULO',axis=0)

Empty DataFrame
Columns: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, ...]
Index: []

[0 rows x 7755 columns]

In [28]:
#criar uma coluna para cada variavel no df de unidades de segurança com as distancias de cada ocorrencia
df_seg_unids['ocorrencia_menos_500m'] = (df_furtos_dist_ocorr < 500).sum()
#df_seg_unids.head()


In [29]:
df_seg_unids['ocorrencia_500_ate_1km'] = df_furtos_dist_ocorr[(df_furtos_dist_ocorr >= 500) & (df_furtos_dist_ocorr <= 1000)].count()



In [30]:
df_seg_unids['ocorrencia_1_ate_1500m'] = df_furtos_dist_ocorr[(df_furtos_dist_ocorr > 1000) & (df_furtos_dist_ocorr <= 1500)].count()



In [31]:
df_seg_unids.head()



eq_tema   eq_esfera        eq_classe   eq_rede   eq_tipo  \
0  SEGURANCA  SEM ESFERA  POLICIA MILITAR  SEM REDE  SEM TIPO   
1  SEGURANCA  SEM ESFERA  POLICIA MILITAR  SEM REDE  SEM TIPO   
2  SEGURANCA  SEM ESFERA  POLICIA MILITAR  SEM REDE  SEM TIPO   
3  SEGURANCA  SEM ESFERA  POLICIA MILITAR  SEM REDE  SEM TIPO   
4  SEGURANCA  SEM ESFERA  POLICIA MILITAR  SEM REDE  SEM TIPO   

                                               DESCR               LOGRADOURO  \
0  1º 6ºPELOTÃO DA 2ªCOMPANHIA DO 34ªBATALHÃO DA ...   AV AFRANIO PEIXOTO 390   
1        ACADEMIA DE POLÍCIA MILITAR DO BARRO BRANCO        AV AGUA FRIA 1923   
2  5ªCOMPANHIA DE POLÍCIA MILITAR-  - SÃO PAULO -...     AV AIRTON PRETINI 69   
3                                  SEDE DO  7º BPM/M         AV ANGELICA 1647   
4  50°BATALHÃO DA POLÍCIA MILITAR -   SÃO PAULO -...  AV CARLOS OBERHUBER 397   

                 eq_bairro     eq_cep  eq_cd_tema  ...  eq_cd_clas  \
0                  BUTANTÃ  5507000.0           7  ...           5   
1                ÁGUA FRIA        NaN           7  ...           5   
2  JARDIM AMÉRICA DA PENHA  3090000.0           7  ...           5   
3            SANTA CECÍLIA  1301000.0           7  ...           5   
4            VILA SÃO JOSÉ        NaN           7  ...           5   

   eq_cd_rede  eq_cd_tipo   eq_id   LATITUDE  LONGITUDE             TIPO  \
0           0           0  150458 -23.567232 -46.709141  Policia Militar   
1           0           0  150288 -23.472852 -46.619790  Policia Militar   
2           0           0  150388 -23.529125 -46.554456  Policia Militar   
3           0           0  150472 -23.547012 -46.658066  Policia Militar   
4           0           0  150294 -23.741673 -46.709250  Policia Militar   

  ocorrencia_menos_500m  ocorrencia_500_ate_1km  ocorrencia_1_ate_1500m  
0                     0                       0                       0  
1                     0                       0                       1  
2                     1                       1                       0  
3                     0                       0                       0  
4                     0                       3                       1  

[5 rows x 21 columns]

In [32]:
#salvar o CSV
df_seg_unids.to_csv('dados/df_seg_unids_dist.csv', index = False,sep=';')

Somar as colunas 

In [210]:
column_names = ['ocorrencia_menos_500m','ocorrencia_500_ate_1km','ocorrencia_1_ate_1500m']
df_seg_unids[column_names].sum(axis=0)

ocorrencia_menos_500m     159
ocorrencia_500_ate_1km    455
ocorrencia_1_ate_1500m    682
dtype: int64

In [ ]:
A analise confirma que quanto mais próximo de uma unidade de segurança, menos furtos ocorrem.